# Core Particle

Ellipsoid/Sphere in 2D/3D

This is optional

In [1]:
import trimesh
import pymeshlab
import numpy as np
import plotly.graph_objects as go

In [2]:
m = trimesh.creation.icosphere(subdivisions=4, radius=1.0)
m.apply_scale([1.0, 1.0, 2.0])

diag = np.linalg.norm(m.bounds[1] - m.bounds[0])
ms = pymeshlab.MeshSet()
ms.add_mesh(pymeshlab.Mesh(m.vertices, m.faces))
ms.meshing_isotropic_explicit_remeshing(
    targetlen=pymeshlab.PureValue(0.1 * diag),
    iterations=10
)
rm = ms.current_mesh()
m2 = trimesh.Trimesh(vertices=rm.vertex_matrix(), faces=rm.face_matrix(), process=False)

print(m.vertices.shape, m2.vertices.shape)



v = m2.vertices
f = m2.faces
fig = go.Figure(data=[go.Mesh3d(
    x=v[:,0], y=v[:,1], z=v[:,2],
    i=f[:,0], j=f[:,1], k=f[:,2],
    opacity=1.0
)])
fig.update_layout(scene_aspectmode="data")
fig.show()

(2562, 3) (98, 3)


# Exterior

Spherical asperities in 2D/3D

In [84]:
def num_trimesh_vertices(subdivisions):
    # count the number of vertices for a set number of subdivisions
    return 10 * 4 ** subdivisions + 2

def num_trimesh_subdivisions(num_vertices):
    # count the number of subdisions to get a set number of vertices
    s = round(np.log10((num_vertices - 2) / 10) / np.log10(4))
    return max(s, 0)  # clip to 0

def generate_asperities(asperity_radius, particle_radius, target_num_vertices, aspect_ratio=[1.0, 1.0, 1.0], add_core=False):
    # builds the locations of all the asperities on the surface of an ellipsoidal particle
    # the asperities will all have uniform radius and will decorate the surface of an icosphere mesh
    # the icosphere mesh will be initially generated for a sphere with a set number of subdivisions
    # the number of subdivisions is suggested from the desired number of vertices
    # the icosphere mesh is then scaled by the aspect ratio to give an ellipsoid
    if len(aspect_ratio) != 3:
        raise ValueError(f'Error: aspect ratio must be a 3-length list-like.  Expected 3, got {len(aspect_ratio)}')
    aspect_ratio = np.array(aspect_ratio)
    if asperity_radius > particle_radius:
        print(f'Warning: asperity radius exceeds particle radius.  {asperity_radius} > {particle_radius}')
    core_radius = particle_radius - asperity_radius
    m = trimesh.creation.icosphere(subdivisions=num_trimesh_subdivisions(target_num_vertices), radius=core_radius)
    m.apply_scale(aspect_ratio)
    asperity_positions = m.vertices
    asperity_radii = np.ones(m.vertices.shape[0]) * asperity_radius
    if add_core:
        if np.all(aspect_ratio == 1.0):  # sphere branch
            asperity_positions = np.concatenate((asperity_positions, np.zeros((1, 3))), axis=0)
            asperity_radii = np.concatenate((asperity_radii, np.array([core_radius])), axis=0)
        else:
            print('Warning: ellipsoid core not yet supported')
    return asperity_positions, asperity_radii

def generate_mesh(asperity_positions, asperity_radii, subdivisions):
    meshes = []
    for a, r in zip(asperity_positions, asperity_radii):
            m = trimesh.creation.icosphere(subdivisions=subdivisions, radius=r)
            m.apply_translation(a)
            meshes.append(m)
    mesh = trimesh.util.concatenate(meshes)
    assert (mesh.is_winding_consistent & mesh.is_watertight)
    return mesh

In [175]:
asperity_radius = 0.2
particle_radius = 0.5
nv = 20
aspect_ratio = [1.0, 1.0, 1.0]

asperity_positions, asperity_radii = generate_asperities(
    asperity_radius=asperity_radius,
    particle_radius=particle_radius,
    target_num_vertices=nv,
    aspect_ratio=aspect_ratio,
    add_core=True
)

# a_base = trimesh.creation.icosphere(subdivisions=2, radius=asperity_radius)
# a_list = [trimesh.Trimesh(vertices=a_base.vertices + a, faces=a_base.faces) for a in asperity_positions]

mesh = generate_mesh(asperity_positions, asperity_radii, 3)
v = mesh.vertices
f = mesh.faces
fig = go.Figure(data=[go.Mesh3d(
    x=v[:,0], y=v[:,1], z=v[:,2],
    i=f[:,0], j=f[:,1], k=f[:,2],
    opacity=1.0
)])
fig.update_layout(scene_aspectmode="data")
fig.show()


# the particle extent needs to be equal to particle radius * aspect ratio!!!!!!
np.max(mesh.vertices, axis=0) - np.min(mesh.vertices, axis=0), np.array(aspect_ratio) * particle_radius * 2.0

(TrackedArray([0.91039049, 0.91039049, 0.91039049]), array([1., 1., 1.]))

In [ ]:
import jax
from jax.scipy.spatial.transform import Rotation
from jaxdem.utils import Quaternion
import jax.numpy as jnp


def random_unit_quat_3d(key):
    u = jax.random.normal(key, (4,))
    u = u / jnp.linalg.norm(u)
    return Quaternion(w=u[0:1], xyz=u[1:4])

def random_rotate(q, key):
    R = random_unit_quat_3d(key)
    Rb = Quaternion(
        w=jnp.broadcast_to(R.w, q.w.shape),
        xyz=jnp.broadcast_to(R.xyz, q.xyz.shape),
    )
    return Quaternion.unit(Rb @ q)

mass = 1.0
asperity_radius = 0.2
particle_radius = 0.5
nv = 20
aspect_ratio = [1.0, 1.0, 1.0]
add_core = True
mesh_subdivisions = 5

asperity_positions, asperity_radii = generate_asperities(
    asperity_radius=asperity_radius,
    particle_radius=particle_radius,
    target_num_vertices=nv,
    aspect_ratio=aspect_ratio,
    add_core=add_core
)
mesh = generate_mesh(asperity_positions, asperity_radii, mesh_subdivisions)

pos_c = mesh.mass_properties.center_mass
volume = mesh.volume
inertia = 0.5 * (mass / mesh.volume) * (mesh.mass_properties.inertia + mesh.mass_properties.inertia.T)
nv = asperity_positions.shape[0]

# get the body axis frame
vals, vecs = np.linalg.eigh(inertia)
rot = Rotation.from_matrix(vecs)
q_xyzw = rot.as_quat()
q_update = jnp.concatenate([q_xyzw[3:4], q_xyzw[:3]])
q_update = jnp.stack([q_update for i in range(nv)])
q = Quaternion(q_update[..., 0:1], q_update[..., 1:])

# save in state
mass = jnp.ones(nv) * mass
volume = jnp.ones(nv) * volume
pos_c = jnp.stack([pos_c for i in range(nv)])
inertia = jnp.stack([vals for i in range(nv)])
q
pos_p = q.rotate_back(q, asperity_positions - pos_c)

# randomly rotate
seed = np.random.randint(0, 1e9)
key = jax.random.PRNGKey(seed)
q = random_rotate(q, key)
pos_p = q.rotate_back(q, asperity_positions - pos_c)

Array([[-2.48756468e-01,  1.46412045e-01, -8.17540139e-02],
       [-1.56148538e-01,  1.32139921e-01,  2.19446331e-01],
       [ 1.56148538e-01, -1.32139921e-01, -2.19446331e-01],
       [ 2.48756468e-01, -1.46412045e-01,  8.17540139e-02],
       [-1.09817721e-02, -2.99603641e-01, -1.08200014e-02],
       [-2.61226833e-01, -1.27449021e-01,  7.42785335e-02],
       [ 2.61226833e-01,  1.27449021e-01, -7.42785335e-02],
       [ 1.09817721e-02,  2.99603641e-01,  1.08200014e-02],
       [ 1.59038514e-01,  1.20420136e-01,  2.24066421e-01],
       [-9.19568539e-03, -1.43512920e-01,  2.63285935e-01],
       [ 9.19568539e-03,  1.43512920e-01, -2.63285935e-01],
       [-1.59038514e-01, -1.20420136e-01, -2.24066421e-01],
       [-2.52890041e-18, -1.04807771e-17, -9.12713321e-18]],      dtype=float32)

In [ ]:



# check if the aspect ratio is that of a sphere
# if so, just return a single sphere
core_voxel_radius = 0.05
target_num_vertices = 1000
core_radius = particle_radius - asperity_radius  - core_voxel_radius
print(core_radius)
if core_radius < 0:
    raise ValueError(f'Error: voxel radius + asperity radius > particle radius.  Core cannot be constructed.')
m = trimesh.creation.icosphere(subdivisions=num_trimesh_subdivisions(target_num_vertices), radius=core_radius)
m.apply_scale(aspect_ratio)


a_base = trimesh.creation.icosphere(subdivisions=2, radius=core_voxel_radius)
a_list = [trimesh.Trimesh(vertices=a_base.vertices + a, faces=a_base.faces) for a in m.vertices]
merged = trimesh.util.concatenate(a_list, merged)
# the particle extent needs to be equal to particle radius * aspect ratio!!!!!!
np.max(merged.vertices, axis=0) - np.min(merged.vertices, axis=0)


v = merged.vertices
f = merged.faces
fig = go.Figure(data=[go.Mesh3d(
    x=v[:,0], y=v[:,1], z=v[:,2],
    i=f[:,0], j=f[:,1], k=f[:,2],
    opacity=1.0
)])
fig.update_layout(scene_aspectmode="data")
fig.show()


0.35000000000000003


In [92]:
m.vertices.shape, 10 * 4 ** 0 + 2

((12, 3), 12)